# Tolerant Slicing

Out-of-bounds indices specified during slicing will be "snapped to the ends of the array" instead of throwing out of range exception. This will improve usability for certain use cases.

In [ ]:
let xs = [1;2;3]

xs.[3..4].Count()

In [2]:
xs.[0..4]

index value 0 1 1 2 2 3

In [7]:
open System

// We know this contains a 512x512 raw bitmap, there might be padding bits at the end but we really don't care about those
let image = ( 
    (System.IO.File.ReadAllBytes("lena_gray.raw")) 
             |> Seq.map( fun i -> (int) i) 
            ).ToArray()

In [9]:
let width = 512

In [10]:
let image2d = ([0..512] |> Seq.map(fun start -> image.[(start*width)..((start+1)*width - 1)])).ToArray()

In [12]:
open XPlot.Plotly

Heatmap(
    z = image2d,
    colorscale = "Greys"
)
|> Chart.Plot
|> Chart.WithWidth 512
|> Chart.WithHeight 512

# 3D/4D Fixed Index Slicing

For slices on 3D/4D arrays, our APIs only take ranges for each of the arguments. This means that it was impossible to extract an array of lower dimension from a 3D/4D array before.

In [24]:
#r "nuget:SixLabors.ImageSharp, version=1.0.0-beta0007"

In [40]:
open SixLabors.ImageSharp;
open SixLabors.ImageSharp.Advanced;

In [51]:
let x: Image<PixelFormats.Rgba32> = Image.Load("underwater_bmx.png")

In [90]:
let colorImg =  (([0..x.Height-1] 
    |> List.map(fun h -> 
        let row = x.GetPixelRowSpan(h).ToArray()
        row |> Array.map(fun i -> [| (int) i.R; (int) i.G; (int)i.B |]))
).ToArray())
   

In [92]:
let array3d (arrs: 'a array array array ) = Array3D.init arrs.Length arrs.[0].Length arrs.[0].[0].Length  (fun i j k -> arrs.[i].[j].[k])

let colorImg3D = array3d colorImg

In [98]:
open XPlot.Plotly

Heatmap(
    z = colorImg3D.[*, *, 0],
    colorscale = "Reds"
)
|> Chart.Plot
|> Chart.WithWidth 1076
|> Chart.WithHeight 773

In [97]:
open XPlot.Plotly

Heatmap(
    z = colorImg3D.[*, *, 1],
    colorscale = "Blues"
)
|> Chart.Plot
|> Chart.WithWidth 1076
|> Chart.WithHeight 773

# From-the-end Slicing

Users can now specify indices with `^` to obtain a slice from the end, similar to C#.

In [108]:
let imageTrimmed = array2D (image2d.[0..511])

In [109]:
let y = imageTrimmed.[^250.., ^250..]

In [112]:
Heatmap(
    z = y,
    colorscale = "Greys"
)
|> Chart.Plot
|> Chart.WithWidth 512
|> Chart.WithHeight 512

In [131]:
type Foo() =
    member x.GetReverseIndex(_rank: int, idx: string) = idx + " reversed"
    member x.GetSlice(a: string option, b: string option) = a.ToString() + " " + b.ToString()
    
let a = Foo()

In [134]:
a.["a"..^"b"]

Some(a) Some(b reversed)

Some(a) Some(b)